

### Capstone Project - The Battle of the Neighborhoods (Week 2)
* Restaurant Location Selection in New York City in the Face of COVID-19 Risk

Monika Dileep
* Table of contents

    Introduction: Business Problem
    Data
    Methodology
    Analysis
    Results and Discussion
    Conclusion




## Introduction: Business Problem

In this project, we will uncover some data information about the relationship between local events and places in New York City and the COVID-19 risk.

We are particularly interested in the relationship between local events and places and COVID-19 Case Rate(per 10k) in different NYC neigbhorhoods.

We will use exploratory analysis approaches to reveal some interesting features of locations in New York City where we observe lower COVID-19 case rate and where we observe higher case rate. The revealed information will help people who are considering to open new restaurants or relocating their restaurants in New York City.


In [ ]:
Data: Gathering required data 

### Installing beautiful soup to download data set

In [1]:
!pip install BeautifulSoup4
!pip install requests


In [2]:
#imports
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np

#get html from wiki page and create soup object
source = requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")
soup = BeautifulSoup(source.text, 'lxml')

#using soup object, iterate the .wikitable to get the data from the HTML page and store it into a list
data = []
columns = []
table = soup.find(class_='wikitable')
for index, tr in enumerate(table.find_all('tr')):
    section = []
    for td in tr.find_all(['th','td']):
        section.append(td.text.rstrip())
    
    #First row of data is the header
    if (index == 0):
        columns = section
    else:
        data.append(section)

#convert list into Pandas DataFrame
canada_df = pd.DataFrame(data = data,columns = columns)
canada_df.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [3]:
canada_df = canada_df[canada_df['Borough'] != 'Not assigned']
canada_df.head()


Postal Code           Borough                                 Neighborhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [4]:
canada_df["Neighborhood"] = canada_df.groupby("Postal Code")["Neighborhood"].transform(lambda neigh: ', '.join(neigh))

#remove duplicates
canada_df = canada_df.drop_duplicates()

#update index to be postcode if it isn't already
if(canada_df.index.name != 'Postal Code'):
    canada_df = canada_df.set_index('Postal Code')
    
canada_df.head()

Borough                                 Neighborhood
Postal Code                                                               
M3A                North York                                    Parkwoods
M4A                North York                             Victoria Village
M5A          Downtown Toronto                    Regent Park, Harbourfront
M6A                North York             Lawrence Manor, Lawrence Heights
M7A          Downtown Toronto  Queen's Park, Ontario Provincial Government

In [5]:
canada_df['Neighborhood'].replace("Not assigned", canada_df["Borough"],inplace=True)
canada_df.head()

Borough                                 Neighborhood
Postal Code                                                               
M3A                North York                                    Parkwoods
M4A                North York                             Victoria Village
M5A          Downtown Toronto                    Regent Park, Harbourfront
M6A                North York             Lawrence Manor, Lawrence Heights
M7A          Downtown Toronto  Queen's Park, Ontario Provincial Government

In [6]:
canada_df.shape

(103, 2)

In [7]:
df=pd.read_csv('http://cocl.us/Geospatial_data')
df.head()


Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

### Analysis

Methodology

I employed two exploratory data analysis methods in my project.

The first is Choropleth map using folium library that visualizes the COVID-19 case rate(per 10k) in different neighborhoods of New York City.

The second is K-means clustering that will partition neighborhoods into different clusters based on the group of venues associated with the neighborhoods. As such, neighborhoods in the same cluster are more similar to one another; neighborhoods in different clusters are more dissimilar to one another.

After the K-means clustering is completed, we also summary the 1st, 2nd, and 3rd most common venues in each of the resulted clusters. We then add the clustering results to the Choropleth map created above.


In [11]:


import folium



In [12]:
df = df.set_index('Postal Code')


In [13]:
df_combined = pd.concat([canada_df, df], axis=1, join='inner')

df_combined.index.name = 'Postal Code'
df_combined.reset_index(inplace=True)

df_combined.head()


Postal Code           Borough                                 Neighborhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [15]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="tl-toronto-neigh")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The co-ordinates of Toronto are {}, {}.'.format(latitude, longitude))

The co-ordinates of Toronto are 43.6534817, -79.3839347.


In [17]:
map_nyc = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, long, post, borough, neigh in zip(df_combined['Latitude'], df_combined['Longitude'], df_combined['Postal Code'], df_combined['Borough'], df_combined['Neighborhood']):
    label = "{} ({}): {}".format(borough, post, neigh)
    popup = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius=5,
        popup=popup,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_nyc)
    
map_nyc

### using Foursquare API

In [18]:
CLIENT_ID = 'ICGN500MVNEILJQCA2KHQWSWUPFMRM355UXF2UXTN0A0Q535' # your Foursquare ID
CLIENT_SECRET = 'QVE353XBYT412ETVKQQRMSRHOM04ZVSVSNP00WRA2HBHMHMA' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ICGN500MVNEILJQCA2KHQWSWUPFMRM355UXF2UXTN0A0Q535
CLIENT_SECRET:QVE353XBYT412ETVKQQRMSRHOM04ZVSVSNP00WRA2HBHMHMA


In [ ]:
radius = 500
LIMIT = 100

venues = []

for lat, long, post, borough, neighborhood in zip(df_combined['Latitude'],df_combined['Longitude'],df_combined['Postal Code'],df_combined['Borough'], df_combined['Neighborhood']):
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    for venue in results:
        venues.append((
            post, 
            borough,
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))
    
    
    

In [20]:
venues_df = pd.DataFrame(venues)
venues_df.columns = ['PostalCode', 'Borough', 'Neighborhood', 'BoroughLatitude', 'BoroughLongitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

venues_df.head()

PostalCode     Borough      Neighborhood  BoroughLatitude  BoroughLongitude  \
0        M3A  North York         Parkwoods        43.753259        -79.329656   
1        M3A  North York         Parkwoods        43.753259        -79.329656   
2        M3A  North York         Parkwoods        43.753259        -79.329656   
3        M4A  North York  Victoria Village        43.725882        -79.315572   
4        M4A  North York  Victoria Village        43.725882        -79.315572   

                VenueName  VenueLatitude  VenueLongitude      VenueCategory  
0         Brookbanks Park      43.751976      -79.332140               Park  
1         GTA Restoration      43.753396      -79.333477    Fireworks Store  
2           Variety Store      43.751974      -79.333114  Food & Drink Shop  
3  Victoria Village Arena      43.723481      -79.315635       Hockey Arena  
4             Tim Hortons      43.725517      -79.313103        Coffee Shop

In [21]:
venues_df.groupby(['PostalCode', 'Borough', 'Neighborhood'])['VenueName'].count()


PostalCode  Borough           Neighborhood                                                 
M1B         Scarborough       Malvern, Rouge                                                     1
M1C         Scarborough       Rouge Hill, Port Union, Highland Creek                             2
M1E         Scarborough       Guildwood, Morningside, West Hill                                  7
M1G         Scarborough       Woburn                                                             3
M1H         Scarborough       Cedarbrae                                                          8
M1J         Scarborough       Scarborough Village                                                2
M1K         Scarborough       Kennedy Park, Ionview, East Birchmount Park                        5
M1L         Scarborough       Golden Mile, Clairlea, Oakridge                                   10
M2H         North York        Hillcrest Village                                                  5
M2J         North

In [22]:
# one hot encoding
combined_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add postal, borough and neighborhood column back to dataframe
combined_onehot['PostalCode'] = venues_df['PostalCode'] 
combined_onehot['Borough'] = venues_df['Borough'] 
combined_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move postal, borough and neighborhood column to the first column
fixed_columns = list(combined_onehot.columns[-3:]) + list(combined_onehot.columns[:-3])
combined_onehot = combined_onehot[fixed_columns]

print(combined_onehot.shape)
combined_onehot.head()


(1130, 223)


PostalCode     Borough     Neighborhoods  Accessories Store  Airport  \
0        M3A  North York         Parkwoods                  0        0   
1        M3A  North York         Parkwoods                  0        0   
2        M3A  North York         Parkwoods                  0        0   
3        M4A  North York  Victoria Village                  0        0   
4        M4A  North York  Victoria Village                  0        0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                    0             0         0            0           0   
1                    0             0         0            0           0   
2                    0             0         0            0           0   
3                    0             0         0            0           0   
4                    0             0         0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                    0                 0                   0          0   
1                    0                 0                   0          0   
2                    0                 0                   0          0   
3                    0                 0                   0          0   
4                    0                 0                   0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Baseball Stadium  Basketball Stadium  Beach  Beer Bar  Beer Store  \
0                 0                   0      0         0           0   
1                 0                   0      0         0           0   
2                 0                   0      0         0           0   
3                 0                   0      0         0           0   
4                 0                   0      0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Bookstore  Boutique  \
0                   0          0       0          0         0   
1                   0          0       0          0         0   
2                   0          0       0          0         0   
3                   0          0       0          0         0   
4                   0          0       0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0             0              0         0   
2                0         0             0              0         0   
3                0         0             0              0         0   
4                0         0             0              0         0   

   Bus Station  Business Service  Cafeteria  Café  Camera Store  Candy Store  \
0            0                 0          0     0             0            0   
1            0                 0          0     0             0            0   
2            0                 0          0     0             0            0   
3            0                 0          0     0             0            0   
4            0                 0          0     0             0            0   

   Caribbean Restaurant  Cheese Shop  Chinese Restaurant  Chocolate Shop  \
0                     0            0                   0               

In [23]:
combined_freq = combined_onehot.groupby(['PostalCode', 'Borough', 'Neighborhoods']).mean().reset_index()

combined_freq.head()

PostalCode      Borough                           Neighborhoods  \
0        M1B  Scarborough                          Malvern, Rouge   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek   
2        M1E  Scarborough       Guildwood, Morningside, West Hill   
3        M1G  Scarborough                                  Woburn   
4        M1H  Scarborough                               Cedarbrae   

   Accessories Store  Airport  American Restaurant  Antique Shop  Aquarium  \
0                0.0      0.0                  0.0           0.0       0.0   
1                0.0      0.0                  0.0           0.0       0.0   
2                0.0      0.0                  0.0           0.0       0.0   
3                0.0      0.0                  0.0           0.0       0.0   
4                0.0      0.0                  0.0           0.0       0.0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0          0.0         0.0                  0.0               0.0   
1          0.0         0.0                  0.0               0.0   
2          0.0         0.0                  0.0               0.0   
3          0.0         0.0                  0.0               0.0   
4          0.0         0.0                  0.0               0.0   

   Athletics & Sports  BBQ Joint  Baby Store  Bagel Shop  Bakery      Bank  \
0               0.000        0.0         0.0         0.0   0.000  0.000000   
1               0.000        0.0         0.0         0.0   0.000  0.000000   
2               0.000        0.0         0.0         0.0   0.000  0.142857   
3               0.000        0.0         0.0         0.0   0.000  0.000000   
4               0.125        0.0         0.0         0.0   0.125  0.125000   

   Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  Beer Bar  \
0  0.0             0.0               0.0                 0.0    0.0       0.0   
1  0.5             0.0               0.0                 0.0    0.0       0.0   
2  0.0             0.0               0.0                 0.0    0.0       0.0   
3  0.0             0.0               0.0                 0.0    0.0       0.0   
4  0.0             0.0               0.0                 0.0    0.0       0.0   

   Beer Store  Belgian Restaurant  Bike Shop  Bistro  Bookstore  Boutique  \
0         0.0                 0.0        0.0     0.0        0.0       0.0   
1         0.0                 0.0        0.0     0.0        0.0       0.0   
2         0.0                 0.0        0.0     0.0        0.0       0.0   
3         0.0                 0.0        0.0     0.0        0.0       0.0   
4         0.0                 0.0        0.0     0.0        0.0       0.0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                   0.0        0.000000      0.0          0.0   
1                   0.0        0.000000      0.0          0.0   
2                   0.0        0.142857      0.0          0.0   
3                   0.0        0.000000      0.0          0.0   
4                   0.0        0.000000      0.0          0.0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0              0.0       0.0           0.0            0.0       0.0   
1              0.0       0.0           0.0            0.0       0.0   
2              0.0       0.0           0.0            0.0       0.0   
3              0.0       0.0           0.0            0.0       0.0   
4              0.0       0.0           0.0            0.0       0.0   

   Bus Station  Business Service  Cafeteria  Café  Camera Store  Candy Store  \
0          0.0               0.0        0.0   0.0           0.0          0.0   
1          0.0               0.0        0.0   0.0           0.0          0.0   
2          0.0               0.0        0.0   0.0           0.0          0.0   
3          0.0               0.0        0.0   0.0           0.0          0.0   
4          0.0               0.0        0.0   0.0           0.0   

In [24]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
areaColumns = ['PostalCode', 'Borough', 'Neighborhoods']
freqColumns = []
for ind in np.arange(num_top_venues):
    try:
        freqColumns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        freqColumns.append('{}th Most Common Venue'.format(ind+1))
columns = areaColumns+freqColumns
# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['PostalCode'] = combined_freq['PostalCode']
neighborhoods_venues_sorted['Borough'] = combined_freq['Borough']
neighborhoods_venues_sorted['Neighborhoods'] = combined_freq['Neighborhoods']

for ind in np.arange(combined_freq.shape[0]):
    row_categories = combined_freq.iloc[ind, :].iloc[3:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    neighborhoods_venues_sorted.iloc[ind, 3:] = row_categories_sorted.index.values[0:num_top_venues]

neighborhoods_venues_sorted.sort_values(freqColumns, inplace=True)
neighborhoods_venues_sorted

PostalCode           Borough  \
17        M3K        North York   
41        M6H      West Toronto   
4         M1H       Scarborough   
10        M2K        North York   
2         M1E       Scarborough   
42        M6J      West Toronto   
7         M1L       Scarborough   
11        M2L        North York   
43        M6K      West Toronto   
30        M5C  Downtown Toronto   
9         M2J        North York   
29        M5B  Downtown Toronto   
36        M6A        North York   
34        M5J  Downtown Toronto   
15        M3H        North York   
32        M5G  Downtown Toronto   
31        M5E  Downtown Toronto   
23        M4G         East York   
35        M5K  Downtown Toronto   
3         M1G       Scarborough   
28        M5A  Downtown Toronto   
33        M5H  Downtown Toronto   
44        M7A  Downtown Toronto   
1         M1C       Scarborough   
6         M1K       Scarborough   
8         M2H        North York   
0         M1B       Scarborough   
38        M6C              York   
12        M3A        North York   
16        M3J        North York   
26        M4K      East Toronto   
40        M6G  Downtown Toronto   
19        M4A        North York   
18        M3L        North York   
13        M3B        North York   
22        M4E      East Toronto   
25        M4J         East York   
39        M6E              York   
20        M4B         East York   
45        M9C         Etobicoke   
37        M6B        North York   
5         M1J       Scarborough   
27        M4L      East Toronto   
24        M4H         East York   
21        M4C         East York   
14        M3C        North York   

                                        Neighborhoods  \
17                                          Downsview   
41                       Dufferin, Dovercourt Village   
4                                           Cedarbrae   
10                                    Bayview Village   
2                   Guildwood, Morningside, West Hill   
42                           Little Portugal, Trinity   
7                     Golden Mile, Clairlea, Oakridge   
11                           York Mills, Silver Hills   
43       Brockton, Parkdale Village, Exhibition Place   
30                                     St. James Town   
9                        Fairview, Henry Farm, Oriole   
29                           Garden District, Ryerson   
36                   Lawrence Manor, Lawrence Heights   
34  Harbourfront East, Union Station, Toronto Islands   
15    Bathurst Manor, Wilson Heights, Downsview North   
32                                 Central Bay Street   
31                                        Berczy Park   
23                                            Leaside   
35           Toronto Dominion Centre, Design Exchange   
3                                              Woburn   
28                          Regent Park, Harbourfront   
33                           Richmond, Adelaide, King   
44        Queen's Park, Ontario Provincial Government   
1              Rouge Hill, Port Union, Highland Creek   
6         Kennedy Park, Ionview, East Birchmount Park   
8                                   Hillcrest Village   
0                                      Malvern, Rouge   
38                                 Humewood-Cedarvale   
12                                          Parkwoods   
16                    Northwood Park, York University   
26                       The Danforth West, Riverdale   
40                                           Christie   
19                                   Victoria Village   
18                                          Downsview   
13                                          Don Mills   
22                                        The Beaches   
25      East Toronto, Broadview North (Old East York)   
39                                Caledonia-Fairbanks   
20                    Parkview Hill, Woodbine Gardens   
45  Eringate, Bloordale Gardens, Old Burnhamthorpe...   
37                  

In [37]:
kclusters = 4

combined_freq_clustering = combined_freq.drop(['PostalCode', 'Borough', 'Neighborhoods'], 1)

kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(combined_freq_clustering)

kmeans.labels_[0:11]


array([2, 3, 0, 0, 0, 3, 0, 0, 0, 0, 0], dtype=int32)

In [ ]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
nyc_merged = nyc_neighborhoods
nyc_merged = nyc_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
nyc_merged = nyc_merged.dropna(subset=['Cluster Labels'])

# identify the top 3 most common venues in each cluster (the top 3 venues are not necessarily different in one cluster)
first=nyc_merged[["Cluster Labels", "1st Most Common Venue"]].groupby(['Cluster Labels']).agg(lambda x:x.value_counts().index[0])
first_venue=first.groupby(['Cluster Labels']).agg(lambda x:x.value_counts().index[0])
first_venue.rename(columns={"1st Most Common Venue": "1st"}, inplace=True)

second=nyc_merged[["Cluster Labels", "2nd Most Common Venue"]].groupby(['Cluster Labels']).agg(lambda x:x.value_counts().index[0])
second_venue=second.groupby(['Cluster Labels']).agg(lambda x:x.value_counts().index[0])
second_venue.rename(columns={"2nd Most Common Venue": "2nd"}, inplace=True)

third=nyc_merged[["Cluster Labels", "3rd Most Common Venue"]].groupby(['Cluster Labels']).agg(lambda x:x.value_counts().index[0])
third_venue=third.groupby(['Cluster Labels']).agg(lambda x:x.value_counts().index[0])
third_venue.rename(columns={"3rd Most Common Venue": "3rd"}, inplace=True)

nyc_merged=pd.merge(nyc_merged, first_venue, on='Cluster Labels', how='left')
nyc_merged=pd.merge(nyc_merged, second_venue, on='Cluster Labels', how='left')
nyc_merged=pd.merge(nyc_merged, third_venue, on='Cluster Labels', how='left')


In [41]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, post, bor, poi in zip(df_combined['Latitude'],df_combined['Longitude'],df_combined['Postal Code'],df_combined['Borough'],df_combined['Neighborhood']):
    label = folium.Popup('{} ({}): {} '.format(bor, post, poi), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow,
        fill=True,
        fill_color=rainbow,
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

One part of our analysis is completed..Next importing COVID 19 data in Newyork City And Analyse

#### Importing COVID DATA

In [42]:
url = 'https://raw.githubusercontent.com/nychealth/coronavirus-data/master/data-by-modzcta.csv'
nyc_COVID19=pd.read_csv(url, error_bad_lines=False)
nyc_COVID19['MODIFIED_ZCTA'] = nyc_COVID19['MODIFIED_ZCTA'].astype('int').astype('str')
nyc_COVID19.head()

MODIFIED_ZCTA                        NEIGHBORHOOD_NAME BOROUGH_GROUP  \
0         10001               Chelsea/NoMad/West Chelsea     Manhattan   
1         10002                Chinatown/Lower East Side     Manhattan   
2         10003  East Village/Gramercy/Greenwich Village     Manhattan   
3         10004                       Financial District     Manhattan   
4         10005                       Financial District     Manhattan   

   COVID_CASE_COUNT  COVID_CASE_RATE  POP_DENOMINATOR  COVID_DEATH_COUNT  \
0               376          1595.72         23563.03                 21   
1              1063          1384.92         76755.41                151   
2               453           841.98         53801.62                 33   
3                31           849.17          3650.61                  1   
4                63           750.35          8396.11                  2   

   COVID_DEATH_RATE  PERCENT_POSITIVE  TOTAL_COVID_TESTS  
0             89.12             14.44               2604  
1            196.73             19.50               5452  
2             61.34             11.25               4028  
3             27.39             10.99                282  
4             23.82             10.19                618

In [43]:
# import NYC geojson file at postalcode level 
# data source: https://data.cityofnewyork.us/Health/Modified-Zip-Code-Tabulation-Areas-MODZCTA-/pri4-ifjk
!wget --quiet --quiet https://filedn.com/lJpzjOtA91quQEpwdrgCvcy/DS%20Capstone%20Project/ModifiedZipCodeTabulationAreasMODZCTA.geojson -O nyc_geojson.geojson

In [44]:
nyc_geo = r'nyc_geojson.geojson' # geojson file
# New York City latitude and longitude values
latitude = 40.7127281
longitude = -74.0060152
# create a plain world map
nyc_map = folium.Map(location=[latitude, longitude], zoom_start=12)

## chloropleteh Map for COVID 19 in NEWYORK city

In [45]:
# generate choropleth map using the COVID-19 Case Rate in New York City
nyc_map.choropleth(
    geo_data=nyc_geo,
    data=nyc_COVID19,
    columns=['MODIFIED_ZCTA', 'COVID_CASE_RATE'],
    key_on='feature.properties.modzcta',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='COVID-19 Case Rate(per 10k) in New York City'
)

/opt/conda/envs/Python36/lib/python3.6/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [46]:
nyc_map


Results and Discussion

As seen in the map above, most neighborhoods belonging to CLuster 5 have relatively lower COVID-19 case rate. The top 3 common venue categories in the cluster is "Restaurant", "Park", and "Coffee shop". It is not a surprise to see "Restaurant" among the top categories since it is the case for all other clusters too. Instead, what's interesting is that "Park" appears to be a very common venue category in the neighborhoods.

On the other hand, from the following map, most neighborhoods belonging to Cluster 1 have relatively higher COVID-19 case rate. "Beach" is the very common venue category among those neighborhoods.

My data analysis reveals some interesting features of locations in New York City where we observe lower COVID-19 case rate and where we observe higher case rate. As suggested by our analysis results, the neighborhoods with more parks have less COVID-19 risk. In contrary, if one neighborhood is near crowded beach, there will be high COVID-19 risk.
Conclusion

In this project, I collected geographical data related to COVID-19 cases and local events and places in New York City. I analyzed the data collection using two exploratory methods, namely, Choropleth map and K-means clustering. The analysis results reveal valuable data information about the relationship betwee the two pieces of data. The revealed information supports meaningful recommendations to people who are considering to open new restaurants or relocating their restaurants in New York City.
